---
CSC 268 Homework #1
---

The objective for this homework assignment is to investigate and reproduce all the steps involved in converting a camera raw image into a standard RGB format.  Producing the perfect image is a somewhat strange mix of the technical and the subjective.  Certain steps are more or less obligatory, albeit with parameters that may at times be tweaked.  On top of these procedures, many photographers will apply one or more manual tweaks to their image until it "looks right".  Some modern phone cameras apply AI algorithms to adjust the raw photo for better looks.

Regardless of motivation, the choices made during photo finishing help to form the meaning of the resulting image.  Accepting a default process merely means ceding the decision-making to somebody else who has chosen for you.  Unfortunately, history shows us that this is not a neutral process.  [This article](https://www.nytimes.com/2019/04/25/lens/sarah-lewis-racial-bias-photography.html) describes systemic racism in the color film industry; please practice self-care and prepare yourself accordingly before reading it.  The challenges have not gone away with the switch to digital:  modern phone cameras can detect and automatically attempt to adjust for multiple different skin tones.

To complete this assignment, you should choose one or more raw images to work with.  You can use one of the examples provided with the labs, or you can pick your own from [this site](https://www.signatureedits.com/free-raw-photos/).  (If you choose to work with more than one photo, try to pick ones with the same file format since they vary between manufacturers and camera models.)  We will be relying on the [RawPy](https://letmaik.github.io/rawpy/api/) python library to provide our interface to the files.  You may also wish to download and experiment with a free [raw photo editing tool](http://rawtherapee.com/).  Although the focus of this assignment is on writing our own code to process the image data, witnessing a program that can already do the same thing can be helpful.

## Part 1: Demosaic

Most digital camera today employ a Bayer color filter array, meaning that the individual color sensors are distributed across the face of the chip, and individual color sensors are offset from each other.  In standard RGB format, each pixel must express values for all three color components at each pixel.  The process of converting Bayer filter output to aligned overlapping color values is known as [demosaicing](https://en.wikipedia.org/wiki/Demosaicing).  You can learn more about the color encoding in your image file using the RawPy methods `num_colors`, `color_desc`, and `raw_color`.

We can go about the process in several ways.  As a first approximation, one might ignore the small position shifts between the different color sensors and simply take all the red sensor values as the red layer, blue as the blue, and then average the two greens.  This will result in a lower resolution image than the original -- half the number of pixels in each direction -- and it ignores the small offset between the sensor locations.

More typically, the unobserved color values are simply filled in via interpolation, generating three color planes the size of the original image.  We'll look at interpolation in more detail later, but for now it will suffice to average the neighboring values (either two or four) from pixels where a measurement was taken.  At the border of the image, some pixels may have only one neighbor with a measured value, so they would just duplicate it.

There are more complicated methods for interpolation and smoothing, but they are beyond the scope of this assignment.  Your goal for this step is to write a Python function `demosaic(raw)` that will return R, G, and B raw color planes (2D NumPy arrays) of the same size, using either of the two approaches above.  This will give you practice with indexing into NumPy arrays.


## Part 2: Color Scaling

The color planes returned by the demosaicing step are still raw linear brightness values as measured by the sensors.  Most cameras have different sensitivity levels for the different colors, so for correct color balance they should be calibrated to each other.  Due to thermal noise in the sensor, even pure black will generate some current, so the level representing black will not be at zero.  And the maximum possible sensor value will vary from camera to camera.  In this phase we will adjust for all these considerations to produce color planes scaled between 0.0 and 1.0.

The RawPy library provides functions with the information needed to complete this step.  You can get the black level intensity from `black_level_per_channel`, and the maximum intensity from `camera_white_level_per_channel` (or if necessary, by looking at the maximum observed value in some area known to be white).  The color balance can come from several sources:  `camera_whitebalance` or `daylight_whitebalance`.  To rescale a channel with original values between `lo` and `hi`, use the formula `(C-lo)/(hi-lo)`.  Make sure that the computation uses floating point arithmetic.  If you need to cut off values outside the expected range, use NumPy's `clip` function.

Experiment with different orders in this stage.  What happens if you do the color balancing before the scaling?  After?  Your goal for this step is to write a Python function `scaling(r,g,b)` that returns the scaled and balanced color planes.  If you want to see what the result looks like, you can use NumPy's `dstack` function to turn them into an MxNx3 image for display.  It probably won't look very good until we finish the next step.

## Part 3: Gamma Correction

The values in the raw file reflect the currents generated in the photosensing chip, and are directly related to the number of photons hitting the sensor.  Our subjective sense of brightness does not grow linearly with the photon count.  Rather, in light areas it takes more photons to create the "same" perception of change in brightness as in a dark area.  Adjusting for this perceptual quirk is known as gamma correction, based on the primary parameter in the equation used.

In principle gamma correction is an adjustable process based upon the value of gamma chosen.  In practice the standard RGB protocol defines a particular setting to be used.  You should implement the standard setting at minimum; if you wish you may experiment with a function that can use other values for gamma.

The standard gamma correction proceeds as follows:  For scaled intensities less than 0.0031308, return 12.92 times the original value.  Otherwise return the original value raised to the power of (1/2.4), then multiplied by 1.055 and finally subtracted by 0.055.  You can use NumPy's `power` function for this step.  Your goal for this part of the assignment is to write a Python function `gamma_correct(c)` that will perform standard gamma correction on the NumPy array `c`.  If you want to enable other values of gamma, make that an optional argument to the function.

## Part 4: Putting It All Together & Optional Adjustments

Your final step for this assignment is to create a single function `calibrate` that will take a `RawPy` object and return a standard RGB image.  You can compare your result to that returned by RawPy's `postprocess` method.  It may not match exactly.  Do the results look good for all the images you have tested?  Does it work for a range of skin colors?

Write a reflection below describing what you have learned through this exploration.

If you wish, there are additional calibration topics you can explore.  Color space calibration adjusts a picture for the precise lighting under which it was taken.  You can read more about it in the blog post linked below.

Saturation adjustment will sometimes create a more natural-looking picture.  This tweaks the vibrancy of all colors in the image either up or down.  You can also read more about it in the blog post linked below.

## Your Reflection

(Fill in your thoughts here.)

## Sources & Links

Portions of this assignment were inspired by [this blog post](https://www.odelama.com/photo/Developing-a-RAW-Photo-by-hand/).

[Wikipedia article on gamma for sRGB](https://en.wikipedia.org/wiki/SRGB)

[RawTherapee download](http://rawtherapee.com/)